In [11]:
import pandas as pd

import h3

import copy

import folium

import random

In [101]:
def Convert_Geometry(Grids):
    
    sample_geometry=list()
    
    for grid in Grids:
        
        geometry=list()
    
        for x in h3.h3_to_geo_boundary(grid):
            
            geometry.append([float(x[1]),float(x[0])])
            
        sample_geometry.append(geometry)
            
    return sample_geometry

def Get_Sapce(grid_array):
    
    arr_normalized=list()
    
    for arr in grid_array:
        
        arr_normalized+=arr
        
    return list(set(arr_normalized))

        
def Grid_normalize(arr):
    
    arr=arr.replace('[','')

    arr=arr.replace(']','')

    arr=arr.replace("'",'')

    arr=arr.replace(" ",'')

    arr=arr.split(',')
    
    return arr
    
def Encode(arr,One_encode):
    
    encode=list()
    
    for g in arr:
        
        encode.append(One_encode[g])
        
    return encode

'''Get batch index'''

def Get_batch(df,batch_size=128):
    
    batch_index=[]
    
    for i in range(batch_size,len(df)+batch_size,batch_size):
        
        batch_index.append(i)
        
    return batch_index

def explode(df, col):
    df[col] = df[col].apply(lambda x: [x] if not isinstance(x, list) else x)
    return df.drop(col, axis=1).join(
        pd.DataFrame(list(df[col])).stack().reset_index(level=1, drop=True).rename(col)
    )



'''Get Neighbor ranges'''

def Get_neighbors(y):
    x=list()
    for y_ in y:
        for y__ in y_:
            x.append(y__)
    return x



In [102]:
df=pd.read_csv('./data/train_df.csv')

df = df.drop(columns='Unnamed: 0')

df['Grids']=df.apply(lambda x:Grid_normalize(x['Grids']),axis=1)

df=df[['TRIP_ID','Grids']]

Stat=copy.copy(df)

Stat=explode(Stat,'Grids')

Stat=Stat.groupby('Grids').count()

Stat['Grids']=Stat.index

Stat=Stat.rename(columns={'TRIP_ID':'Num'})

Stat=Stat.sort_values(by='Num', ascending=False)

Stat=Stat.iloc[:50]


Candidates=list(Stat['Grids'])

OD_Pair=list()

for origin in Candidates:

    for grid in Candidates:

        if grid not in Get_neighbors(h3.hex_range_distances(origin, 20)):

            OD_Pair.append(origin+'-'+grid)

    if len(OD_Pair)>100:

         break








# df['origin']=df.apply(lambda x:x['Grids'][0],axis=1)

# df['destination']=df.apply(lambda x:x['Grids'][-1],axis=1)

# df=df.groupby(['origin','destination']).count()

# df['Transition']=df.index

# df['origin']=df.apply(lambda x:x['Transition'][0],axis=1)

# df['destination']=df.apply(lambda x:x['Transition'][1],axis=1)

# df=df.reset_index(drop=True)

# df=df.rename(index=str, columns={'TRIP_ID': 'Cnt'})

# df=df[['origin','destination','Cnt']]

# df=df.sort_values(by='Cnt', ascending=False)




# 

# for idx,row in df.iterrows():
    
#     OD_Pair.append(row['origin']+'-'+row['destination'])
    
# df 


    


In [103]:
def Check_OD(Grids,OD_Pair):
    
    tag='Fail'
    
    for pair in OD_Pair:
    
        Origin=pair.split('-')[0]
        
        Dest=pair.split('-')[1]
        
        if Origin in Grids:
            
            O_id=Grids.index(Origin)
            
            if Dest in Grids[O_id:]:
                
                tag=pair
                
                break
    return tag

def Get_Eliminate(Grids,pair):
    
    Origin=pair.split('-')[0]
        
    Dest=pair.split('-')[1]
    
    O_id=Grids.index(Origin)
    
    D_id=Grids.index(Dest)
    
    return Grids[O_id:D_id+1]
    
    
    



    
    

In [104]:
df=pd.read_csv('./data/train_df.csv')

df = df.drop(columns='Unnamed: 0')

df['Grids']=df.apply(lambda x:Grid_normalize(x['Grids']),axis=1)

df=df[['TRIP_ID','Grids']]

df['Pair']=df.apply(lambda x:Check_OD(x['Grids'],OD_Pair),axis=1)

Ref=df.loc[df['Pair']!='Fail'].groupby('Pair').count()

Ref['Pair']=Ref.index

Ref=Ref.rename(columns={'TRIP_ID':'Num'})

Ref=Ref.sort_values(by='Num', ascending=False)

Ref=Ref[['Pair','Num']]

Ref=Ref.iloc[:5]

Hot_pair=list()

for idx,row in Ref.iterrows():
    
    Hot_pair.append(row['Pair'])
    
df=df.loc[df['Pair'].isin(Hot_pair)]

df=df.reset_index(drop=True)

df['Grids']=df.apply(lambda x:Get_Eliminate(x['Grids'],x['Pair']),axis=1)

df['Geometry']=df.apply(lambda x:Convert_Geometry(x['Grids']),axis=1)

df['label']=1

df

TRIP_ID                                              Grids  \
0    1393240080620000119  [8a39220f6b2ffff, 8a39220f6b77fff, 8a39220f6b4...   
1    1384006234620000423  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
2    1382288997620000391  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
3    1403301593620000297  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
4    1389082603620000904  [8a39220f020ffff, 8a39220f0277fff, 8a39220f026...   
5    1395687042620000229  [8a39220f020ffff, 8a39220f00effff, 8a39220f00e...   
6    1380125751620000325  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
7    1386488836620000129  [8a39220f020ffff, 8a39220f00effff, 8a39220f001...   
8    1382850204620000233  [8a39220f020ffff, 8a39220f0277fff, 8a39220f026...   
9    1383492607620000031  [8a39220f6b2ffff, 8a39220f6b77fff, 8a39220f6b6...   
10   1392766972620000542  [8a39220f1297fff, 8a39220f174ffff, 8a39220f10d...   
11   1383420878620000901  [8a39220f6b2ffff, 8a39220f6b27fff, 8a39220f6b2...   
12   1396851241620000346  [8a39220f6b2ffff, 8a39220f6b47fff, 8a39220f469...   
13   1381614440620000574  [8a39220f6b2ffff, 8a39220f6b27fff, 8a39220f6b0...   
14   1398995009620000067  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
15   1395555641620000429  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
16   1402390994620000698  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
17   1392070955620000307  [8a39220f020ffff, 8a39220f0277fff, 8a39220f026...   
18   1396603803620000687  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
19   1402788800620000192  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
20   1380786514620000011  [8a39220f020ffff, 8a39220f00e7fff, 8a39220f001...   
21   1397363868620000311  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
22   1400878275620000307  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
23   1386706153620000224  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
24   1399195354620000487  [8a39220f020ffff, 8a39220f021ffff, 8a39220f02f...   
25   1375100993620000340  [8a39220f020ffff, 8a39220f00effff, 8a39220f00e...   
26   1400578492620000698  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
27   1391723384620000332  [8a39220f1297fff, 8a39220f174ffff, 8a39220f175...   
28   1402178770620000360  [8a39220f020ffff, 8a39220f0267fff, 8a39220f034...   
29   1393278909620000171  [8a39220f6b2ffff, 8a39220f6b27fff, 8a39220f6b3...   
..                   ...                                                ...   
534  1376514215620000492  [8a39220f020ffff, 8a39220f0257fff, 8a39220f020...   
535  1402235399620000356  [8a39220f020ffff, 8a39220f00e7fff, 8a39220f001...   
536  1383750573620000129  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
537  1397033818620000904  [8a39220f020ffff, 8a39220f0277fff, 8a39220f026...   
538  1393391588620000669  [8a39220f020ffff, 8a39220f0277fff, 8a39220f034...   
539  1391661755620000640  [8a39220f020ffff, 8a39220f0277fff, 8a39220f034...   
540  1394897343620000697  [8a39220f020ffff, 8a39220f00c7fff, 8a39220f00e...   
541  1388547133620000199  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
542  1374975581620000075  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
543  1386044461620000434  [8a39220f020ffff, 8a39220f0277fff, 8a39220f026...   
544  1391764745620000258  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
545  1374071568620000440  [8a39220f020ffff, 8a39220f00e7fff, 8a39220f001...   
546  1401101574620000027  [8a39220f020ffff, 8a39220f0277fff, 8a39220f034...   
547  1399131946620000476  [8a39220f020ffff, 8a39220f00e7fff, 8a39220f001...   
548  1378869295620000136  [8a39220f020ffff, 8a39220f0277fff, 8a39220f034...   
549  1388499714620000904  [8a39220f020ffff, 8a39220f0207fff, 8a39220f023...   
550  1396268358620000547  [8a39220f020ffff, 8a39220f00e7fff, 8a39220f001...   
551  1401958000620000561  [8a39220f1297fff, 8a39220f1667fff, 8a39220f167...   
552  1388687436620000201  [8a39220f020ffff, 8a39220f00effff, 8a3922

In [105]:
GeoData=list()
         
for idx,row in df.iterrows():
    
    for i in range(len(row['Grids'])):
    
        GeoData.append({"type":"Feature",\
                        "id":row['Grids'][i],\
                        "geometry":{"type":"Polygon",\
                                    "coordinates":[row['Geometry'][i]]
                                   }
                       })
    
GeoJson={"type":"FeatureCollection","features":GeoData}




background = folium.Map([41.148738, -8.612091],tiles='CartoDB positron',zoom_start=12)

'''Zones'''

choropleth1 =folium.Choropleth(
    geo_data=GeoJson,
    fill_color='red',
    fill_opacity=0.5,
    name='Zone').add_to(background)

folium.LayerControl().add_to(background)

background


In [106]:
'''Get Neighbor ranges'''

def Get_neighbors(y):
    x=list()
    for y_ in y:
        for y__ in y_:
            x.append(y__)
    return x
    

def Generate_Anomalous(Grids):
    i=0
    while i<len(Grids):
        
        if random.random() < 0.7:
            i+=1
        else:
            candidates=Get_neighbors(h3.hex_range_distances(Grids[i], 1))
            ano=random.choice(candidates)
            while ano==Grids[i]:
                ano=random.choice(candidates)  
            Grids.insert(i+1,ano)
            i+=1
    return Grids
            
                
                                     
            
    

In [107]:
Anomalous=copy.copy(df)

Anomalous['label']=0

Anomalous['Grids']=Anomalous.apply(lambda x:Generate_Anomalous(x['Grids']),axis=1)

df=pd.concat([df,Anomalous],ignore_index=True)

df.to_csv('./data/train_data.csv')

In [108]:
df

TRIP_ID                                              Grids  \
0     1393240080620000119  [8a39220f6b2ffff, 8a39220f6b77fff, 8a39220f6b4...   
1     1384006234620000423  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
2     1382288997620000391  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
3     1403301593620000297  [8a39220f020ffff, 8a39220f0207fff, 8a39220f022...   
4     1389082603620000904  [8a39220f020ffff, 8a39220f0277fff, 8a39220f026...   
5     1395687042620000229  [8a39220f020ffff, 8a39220f00effff, 8a39220f005...   
6     1380125751620000325  [8a39220f020ffff, 8a39220f0277fff, 8a39220f020...   
7     1386488836620000129  [8a39220f020ffff, 8a39220f00effff, 8a39220f001...   
8     1382850204620000233  [8a39220f020ffff, 8a39220f021ffff, 8a39220f027...   
9     1383492607620000031  [8a39220f6b2ffff, 8a39220f6b77fff, 8a39220f6b6...   
10    1392766972620000542  [8a39220f1297fff, 8a39220f174ffff, 8a39220f174...   
11    1383420878620000901  [8a39220f6b2ffff, 8a39220f6b27fff, 8a39220f6b2...   
12    1396851241620000346  [8a39220f6b2ffff, 8a39220f6b47fff, 8a39220f469...   
13    1381614440620000574  [8a39220f6b2ffff, 8a39220f6b0ffff, 8a39220f6b2...   
14    1398995009620000067  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
15    1395555641620000429  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
16    1402390994620000698  [8a39220f020ffff, 8a39220f021ffff, 8a39220f020...   
17    1392070955620000307  [8a39220f020ffff, 8a39220f0277fff, 8a39220f025...   
18    1396603803620000687  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
19    1402788800620000192  [8a39220f020ffff, 8a39220f022ffff, 8a39220f020...   
20    1380786514620000011  [8a39220f020ffff, 8a39220f021ffff, 8a39220f020...   
21    1397363868620000311  [8a39220f020ffff, 8a39220f0277fff, 8a39220f020...   
22    1400878275620000307  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
23    1386706153620000224  [8a39220f020ffff, 8a39220f0277fff, 8a39220f020...   
24    1399195354620000487  [8a39220f020ffff, 8a39220f021ffff, 8a39220f02f...   
25    1375100993620000340  [8a39220f020ffff, 8a39220f00effff, 8a39220f00c...   
26    1400578492620000698  [8a39220f020ffff, 8a39220f0207fff, 8a39220f00e...   
27    1391723384620000332  [8a39220f1297fff, 8a39220f174ffff, 8a39220f175...   
28    1402178770620000360  [8a39220f020ffff, 8a39220f0267fff, 8a39220f034...   
29    1393278909620000171  [8a39220f6b2ffff, 8a39220f6b27fff, 8a39220f6b3...   
...                   ...                                                ...   
1098  1376514215620000492  [8a39220f020ffff, 8a39220f0257fff, 8a39220f020...   
1099  1402235399620000356  [8a39220f020ffff, 8a39220f00e7fff, 8a39220f005...   
1100  1383750573620000129  [8a39220f020ffff, 8a39220f0207fff, 8a39220f021...   
1101  1397033818620000904  [8a39220f020ffff, 8a39220f0277fff, 8a39220f024...   
1102  1393391588620000669  [8a39220f020ffff, 8a39220f02e7fff, 8a39220f025...   
1103  1391661755620000640  [8a39220f020ffff, 8a39220f0277fff, 8a39220f034...   
1104  1394897343620000697  [8a39220f020ffff, 8a39220f00c7fff, 8a39220f00e...   
1105  1388547133620000199  [8a39220f020ffff, 8a39220f0207fff, 8a39220f020...   
1106  1374975581620000075  [8a39220f020ffff, 8a39220f0277fff, 8a39220f020...   
1107  1386044461620000434  [8a39220f020ffff, 8a39220f0277fff, 8a39220f020...   
1108  1391764745620000258  [8a39220f020ffff, 8a39220f02e7fff, 8a39220f020...   
1109  1374071568620000440  [8a39220f020ffff, 8a39220f00e7fff, 8a39220f000...   
1110  1401101574620000027  [8a39220f020ffff, 8a39220f0277fff, 8a39220f034...   
1111  1399131946620000476  [8a39220f020ffff, 8a39220f00e7fff, 8a39220f001...   
1112  1378869295620000136  [8a39220f020ffff, 8a39220f022ffff, 8a39220f027...   
1113  1388499714620000904  [8a39220f020ffff, 8a39220f0207fff, 8a39220f023...   
1114  1396268358620000547  [8a39220f020ffff, 8a39220f00e7fff, 8a39220f00f...   
1115  1401958000620000561  [8a39220f1297fff, 8a39220f1667fff, 8a39220f167...   
1116  138868743662